In [134]:
import json 
import os
from operator import itemgetter
import pandas as pd
import re
import string 
import nltk.classify.util
from nltk.classify import NaiveBayesClassifier
from nltk.corpus import movie_reviews

In [135]:
with open("korean_user_reviews.json") as f:
    datas = json.loads(f.readlines()[0])

print(datas)

{'235': [], '236': [], '677': ["King's Daughter, Soo Baek Hyang is one of the most entertaining dramas I have seen in a long time. It could it even be used as a framework for how to create an entertaining drama. It has great acting, great pacing, great writing, great chemistry between actors and great costumes. Even though King's Daughter, Soo Baek Hyang did not have the most ravish sets nor a high budget-it was able to do more than most fancy sageuks have done in the past. I was most impressed with the acting in this drama. It was well cast with some veteran sageuk actors and newcomers to the genre. The lead actress Hyeon-jin Seo and actress Woo Seo were spectacular and nuanced in their performance. The most soulful performances were by the veteran actors Jae-ryong Lee as King Moo Ryung and Tae-young Yoon as Koo-Chun. King's Daughter, Soo Baek Hyang had great pacing. The episodes were about 30 minutes each. The story did not drag on as some other dramas of this genre-the wars were sho

In [119]:
path = os.path.join("korean_data.csv")
data = pd.read_csv(path)

def cleanhtml(raw_html):
    clean = re.compile('<.*?>')
    cleantext = re.sub(clean, '', raw_html)
    return cleantext


In [120]:
def tokenize(text):
    """Returns a list of words that make up the text.
    Params: {text: String}
    Returns: List
    """
    return list(filter(str.strip, list(map(lambda x: x, re.findall(r'[a-zA-Z]*', text)))))


In [121]:
def preprocess_text(text):
    text = str(text)
    text = cleanhtml(text)
    text = text.lower()
    text = text.translate(str.maketrans('', '', string.punctuation))
    text = text.strip()
    return text

In [122]:
def build_inverted_index_and_regular_index(data):
    """ Builds an inverted index from the movies
    """
    result = {}
    data_index = {}
    for (index,value) in data['Summary'].items():
        value = preprocess_text(value)
        toks = value.split()
        counts = Counter(toks)
        data_index[index] = counts.items()
        for word, count in counts.items():
            if word not in result.keys():
                result[word] = []
            result[word].append((index, count))
    return (result, data_index)

In [123]:
def preprocess(data):
    for (index,value) in data['Summary'].items():
        value = preprocess_text(value)
        data.loc[index,'Summary'] = value
    return data

In [124]:
data = preprocess(data)

In [127]:
replace_no_space = re.compile("(\")|(\d+)")
replace_with_space =re.compile("(<br\s*/><br\s*/>)|(\-)|(\/)")
no_space = ""
blankspace = " "
def preprocess_reviews(datas):
    for index in datas:
        if len(datas[index])==0:
                datas[index] = []
        else:
            datas[index] = [replace_no_space.sub(no_space, line) for line in datas[index]]
            datas[index] = [replace_with_space.sub(blankspace, line) for line in datas[index]]

    return datas

new_datas = preprocess_reviews(datas)


In [128]:
#print(new_datas['1125'][:3])
line = "All the actors acting are OK because there are too many characters showing up in a drama so it\'s hard to focus in a couple\'s story only. To sum up it\'s OK to watch this drama if you have spare time."
#print(line.replace("\\", ""))
nltk.download('movie_reviews')

["As the English title family honor means that the family holds Korean traditional values. The main focus love stories are the th generation children which consist of  sons and the youngest is the daughter. Even though the family holds the traditional values but the family itself is quite modern where the father married for the nd time because his girlfriend who was at her th was pregnant, the st son was married to much younger wive and being a completely perfect husband in his second marriage, the nd child was the weakness of the family because he talked a lot without thinking first and a womanizer, and the last is the humble and modest daughter being a professor at such a young age but also a widow for  year who couldn't believe in love until Lee Gang seuk Park shi hoocame into her life as her bitter sweet enemy. The story revolves the family is quite unbelievable which can happen in a real life but it's OK to watch. All the actors acting are OK because there are too many characters 

True

In [129]:
def extract_features(word_list):
    return dict([(word, True) for word in word_list])

In [130]:
positive_fileids = movie_reviews.fileids('pos')
negative_fileids = movie_reviews.fileids('neg')

In [131]:
features_positive = [(extract_features(movie_reviews.words(fileids=[f])),
                     'Positive') for f in positive_fileids]
features_negative = [(extract_features(movie_reviews.words(fileids=[f])),
                     'Negative') for f in negative_fileids]

In [132]:
threshold_factor = 0.8
threshold_positive = int(threshold_factor * len(features_positive))
threshold_negative = int(threshold_factor * len(features_negative))

In [133]:
features_train = features_positive[:threshold_positive] + features_negative[:threshold_negative]
features_test = features_positive[threshold_positive:] + features_negative[threshold_negative:]

In [138]:
classifier = NaiveBayesClassifier.train(features_train)

In [139]:
def get_sentiment(datas):
    sentiment_dict = {}
    for index in datas: 
        if len(datas[index])==0:
            sentiment_dict[index] = [{'Reviews': 'N/A', 'Sentiment': 'Positive', 'Probability': 0.0}]
        for review in datas[index]:
            probdist = classifier.prob_classify(extract_features(review.split()))
            if index in sentiment_dict:
                sentiment_dict[index].append({'Reviews': review, 'Sentiment': probdist.max(), 'Probability': round(probdist.prob(probdist.max()), 2)})
            else: 
                sentiment_dict[index] = [{'Reviews': review, 'Sentiment': probdist.max(), 'Probability': round(probdist.prob(probdist.max()), 2)}]
          #  sentiment_dict[index]['Reviews'] = review
          #  probdist = classifier.prob_classify(extract_features(review.split()))
          #  sentiment_dict[index]['Sentiment'] = probdist.max()
          #  sentiment_dict[index]['Probability'] = round(probdist.prob(pred_sentiment), 2)
    return sentiment_dict

In [145]:
sentiment_dict = get_sentiment(new_datas)

In [146]:
def get_sentiment_score(sentiment_dict):
    sentiment_scores = {}
    for index in sentiment_dict:
        sum = 0
        for element in sentiment_dict[index]:
            if element['Sentiment'] == 'Negative':
                sum -= element['Probability']
            else:
                sum += element['Probability']
        sentiment_scores[index] = round(sum/len(sentiment_dict[index]), 2)
    return sentiment_scores

In [147]:
sentiment_scores = get_sentiment_score(sentiment_dict)
print(sentiment_scores)

{'235': 0.0, '236': 0.0, '677': 1.0, '978': 0.0, '921': 1.0, '1449': 0.36, '66': 0.82, '341': 0.85, '575': 0.0, '405': 0.0, '325': 0.0, '999': 0.0, '495': 0.0, '427': 0.76, '183': 0.0, '1465': 0.99, '287': 1.0, '364': 0.0, '1092': 0.25, '1122': 0.85, '591': 0.0, '1332': 0.0, '1272': 0.37, '1389': 0.0, '1330': 0.0, '180': 0.0, '170': 0.85, '1451': 0.0, '653': 0.0, '767': 0.0, '1349': 0.0, '778': 0.95, '199': 0.0, '55': 0.0, '1255': 0.0, '313': 0.0, '426': 0.0, '1246': 0.0, '970': 0.97, '1119': 0.0, '1209': 0.0, '666': 0.8, '962': 0.0, '1424': 0.85, '33': 0.45, '1311': 0.0, '378': 0.0, '303': 0.0, '637': 0.88, '74': 0.0, '1025': 0.0, '1439': 0.0, '1030': 0.0, '1050': 0.39, '136': 1.0, '626': 0.0, '518': 0.0, '1326': 0.71, '492': 0.0, '421': 0.0, '718': 0.0, '276': 0.0, '95': 0.0, '781': 0.93, '693': 0.0, '399': 0.0, '929': 0.0, '822': 0.0, '706': 0.0, '1452': 0.0, '551': 0.0, '1268': 1.0, '57': 0.64, '1354': 0.0, '381': 0.97, '208': 0.0, '455': 0.0, '464': 0.0, '850': 0.0, '1438': 0.0, '

In [150]:
def get_reviews_and_sentiment(datas, sentiment_scores):
    reviews_sent = {}
    for key in datas: 
        if (len(datas[key]) == 0):
            reviews_sent[key] = {'Predicted Sentiment': 'Neutral', 'Sentiment Score': 0.0, 'Reviews': 'There are no reviews for this drama.'}
        elif (sentiment_scores[key]==0.0 and len(datas[key]) > 0):
            if len(datas[key]) < 5:
                reviews_sent[key] = {'Predicted Sentiment': 'Neutral', 'Sentiment Score': sentiment_scores[key], 'Reviews': datas[key]}
            else:
                reviews_sent[key] = {'Predicted Sentiment': 'Neutral', 'Sentiment Score': sentiment_scores[key], 'Reviews': datas[key][:5]}
        elif len(datas[key]) < 5: 
            if (sentiment_scores[key] < 0): 
                reviews_sent[key] = {'Predicted Sentiment': 'Negative', 'Sentiment Score': abs(sentiment_scores[key]), 'Reviews': datas[key]}
            else: 
                reviews_sent[key] = {'Predicted Sentiment': 'Positive', 'Sentiment Score': sentiment_scores[key], 'Reviews': datas[key]}
        else: 
            if (sentiment_scores[key] < 0): 
                reviews_sent[key] = {'Predicted Sentiment': 'Negative', 'Sentiment Score': abs(sentiment_scores[key]), 'Reviews': datas[key][:5]}
            else: 
                reviews_sent[key] = {'Predicted Sentiment': 'Positive', 'Sentiment Score': sentiment_scores[key], 'Reviews': datas[key][:5]}
    return reviews_sent 

In [151]:
reviews_sent = get_reviews_and_sentiment(new_datas, sentiment_scores)
print(reviews_sent)

{'235': {'Sentiment Score': 0.0, 'Predicted Sentiment': 'Neutral', 'Reviews': 'There are no reviews for this drama.'}, '236': {'Sentiment Score': 0.0, 'Predicted Sentiment': 'Neutral', 'Reviews': 'There are no reviews for this drama.'}, '798': {'Sentiment Score': 0.7, 'Predicted Sentiment': 'Positive', 'Reviews': ["Reply  aka Answer me to . Korean TV drama.  Episodes. Summer of .SPOILERS AHEAD!Story: Teenagers go through their final school years on the way to young adulthood. As adults, they reconvene in  for their  year class reunion; while there, they all reflect on their past while their history together unfolds via back story. It's primarily a life story drama about growing up.A half dozen high school kids or so are focused on throughout this show some more than others, along with one young teacher, and one set of parents. The vast majority of the story is told from  to  and takes place against the backdrop of the birth of K Pop. The kids meet at high school, become friends, experi